In [17]:
import matplotlib.pyplot as plt
import numpy as np
import matplotlib.animation as animation
import moviepy.editor as mpy
from moviepy.video.io.bindings import mplfig_to_npimage
from scipy.ndimage.filters import convolve
from IPython.display import HTML
import copy

#dati iniziali

#alpha, beta, gamma, delta, chi, nu, cos21, cos31, cos32, sin21, sin31, sin32 = symbols(u'α β γ δ χ ν c(21) c(31) c(32) s(21) s(31) s(32) ')
punti = 500000
tempo_simulazione = 5

h = tempo_simulazione/punti
g = 9.81
t = 0
framepersec = 60
fps60 = int((1/h)/framepersec) # ogni quanto devo saltare di scrivere i frame per ottenere framepersec  foto in un secondo
l1, l2, l3 = (1, 1, 1)
m1, m2, m3 = (1, 1, 1)

# condizioni iniziali
# angolo iniziale in gradi
grad0_1, grad0_2, grad0_3 =  (45, 30, 24)
theta0_1, theta0_2, theta0_3 =  (grad0_1*2*np.pi / 360 ,grad0_2*2*np.pi / 360 ,grad0_3*2*np.pi / 360)
w0_1, w0_2, w0_3 = ( 0, 0, 0 )
# variabile per contenere q_0 e p_0
u0_plot = []

def stormer_verlet(f, u):
    global t
    u0 = u[0]
    um1 = u[1]
    if(t == 0):
        u0[0:3] += um1[3:6]*h + f(um1, 0)[3:6]*h*h/2
        u0[3:6] = (u0[0:3] - um1[0:3])/h
    # derivazione per ottenere y_1 errore O(h)
    u1 = np.zeros(6)
    u1[0:3] += 2*u0[0:3] - um1[0:3]  + f(u0, t)[3:6]*h*h 
    u1[3:6] += (u1[0:3] - u0[0:3])/h
    u[1] = copy.deepcopy(u0)
    u[0] = copy.deepcopy(u1)
    print(u1)
    return u

def velocity_verlet(f, u):
    s = 1e-14 # valore di soglia per risolvere iterativamente equazione autoconsistente
    diff = [2*s, 2*s, 2*s]
    p = 0
    u0 = u[0]
    y_1 = np.zeros(6)
    # "y_0" prima stima
    y_1[0:3] = u0[0:3] + u0[3:6]*h  + f(u0, t)[3:6]*h*h/2 
    # "y_0" prima stima
    y_1[3:6] = u0[3:6] + f(u0, t)[3:6]*h/2
    add = np.zeros(6)
    while (np.abs(diff[0]) > s or np.abs(diff[1]) > s or np.abs(diff[2]) > s):
        diff = add[3:6]
        add =  f(y_1 + add, t)*h/2
        diff -= add[3:6]
        p += 1
    y_1[3:6]+=add[3:6]
    u[0] = y_1
    return 

def runge_kutta4(f, u):
    u0 = u[0]
    k1 = f(u0, t)*h
    k2 = f(u0 + k1/2, t +h/2)*h
    k3 = f(u0 + k2/2 , t + h/2)*h
    k4 = f(u0 + k3 , t + h)*h
    u0 = (u0 + (k1 + 2*k2 + 2*k3 + k4)/6.0)
    u[0] = u0
    #prpply destructive methods on the object int(u0)
    return u


def eulero_esplicito(f, u):
    u0 = u[0]
    u0 = (u0 + f(u0 , t)*h)
    u[0] = u0
    return u


def f_triple(u, t):
	theta_1, theta_2, theta_3 = u[0], u[1], u[2]
	w1, w2, w3 = u[3], u[4], u[5]

	theta_21 = theta_2 - theta_1
	theta_31 = theta_3 - theta_1
	theta_32 = theta_3 - theta_2

	cos_21, cos_31, cos_32 = (np.cos(theta_21), np.cos(theta_31), np.cos(theta_32))
	sin_21, sin_31, sin_32 = (np.sin(theta_21), np.sin(theta_31), np.sin(theta_32))
	sin_1, sin_2, sin_3 = (np.sin(theta_1), np.sin(theta_2), np.sin(theta_3))
	cos_1, cos_2, cos_3 = (np.cos(theta_1), np.cos(theta_2), np.cos(theta_3))

	dw1 = (m3*(g*sin_3 + l1*w1**2*(cos_1*sin_3 - cos_3*sin_1) + l2*w2**2*(cos_2*sin_3 - cos_3*sin_2))*(cos_21*cos_32*m2 + cos_21*cos_32*m3 - cos_31*m2 - cos_31*m3) - (cos_21*m2 + cos_21*m3 - cos_31*cos_32*m3)*(g*m2*sin_2 + g*m3*sin_2 + l1*m2*w1**2*(cos_1*sin_2 - cos_2*sin_1) + l1*m3*w1**2*(cos_1*sin_2 - cos_2*sin_1) - l3*m3*w3**2*(cos_2*sin_3 - cos_3*sin_2)) + (-cos_32**2*m3 + m2 + m3)*(g*m1*sin_1 + g*m2*sin_1 + g*m3*sin_1 - l2*m2*w2**2*(cos_1*sin_2 - cos_2*sin_1) - l2*m3*w2**2*(cos_1*sin_2 - cos_2*sin_1) - l3*m3*w3**2*(cos_1*sin_3 - cos_3*sin_1)))/(l1*(cos_21**2*m2**2 + 2*cos_21**2*m2*m3 + cos_21**2*m3**2 - 2*cos_21*cos_31*cos_32*m2*m3 - 2*cos_21*cos_31*cos_32*m3**2 + cos_31**2*m2*m3 + cos_31**2*m3**2 + cos_32**2*m1*m3 + cos_32**2*m2*m3 + cos_32**2*m3**2 - m1*m2 - m1*m3 - m2**2 - 2*m2*m3 - m3**2))

	dw2 = (-m3*(g*sin_3 + l1*w1**2*(cos_1*sin_3 - cos_3*sin_1) + l2*w2**2*(cos_2*sin_3 - cos_3*sin_2))*(-cos_21*cos_31*m2 - cos_21*cos_31*m3 + cos_32*m1 + cos_32*m2 + cos_32*m3) - (cos_21*m2 + cos_21*m3 - cos_31*cos_32*m3)*(g*m1*sin_1 + g*m2*sin_1 + g*m3*sin_1 - l2*m2*w2**2*(cos_1*sin_2 - cos_2*sin_1) - l2*m3*w2**2*(cos_1*sin_2 - cos_2*sin_1) - l3*m3*w3**2*(cos_1*sin_3 - cos_3*sin_1)) + (-cos_31**2*m3 + m1 + m2 + m3)*(g*m2*sin_2 + g*m3*sin_2 + l1*m2*w1**2*(cos_1*sin_2 - cos_2*sin_1) + l1*m3*w1**2*(cos_1*sin_2 - cos_2*sin_1) - l3*m3*w3**2*(cos_2*sin_3 - cos_3*sin_2)))/(l2*(cos_21**2*m2**2 + 2*cos_21**2*m2*m3 + cos_21**2*m3**2 - 2*cos_21*cos_31*cos_32*m2*m3 - 2*cos_21*cos_31*cos_32*m3**2 + cos_31**2*m2*m3 + cos_31**2*m3**2 + cos_32**2*m1*m3 + cos_32**2*m2*m3 + cos_32**2*m3**2 - m1*m2 - m1*m3 - m2**2 - 2*m2*m3 - m3**2))

	dw3 = ((g*sin_3 + l1*w1**2*(cos_1*sin_3 - cos_3*sin_1) + l2*w2**2*(cos_2*sin_3 - cos_3*sin_2))*(-cos_21**2*m2**2 - 2*cos_21**2*m2*m3 - cos_21**2*m3**2 + m1*m2 + m1*m3 + m2**2 + 2*m2*m3 + m3**2) + (cos_21*cos_32*m2 + cos_21*cos_32*m3 - cos_31*m2 - cos_31*m3)*(g*m1*sin_1 + g*m2*sin_1 + g*m3*sin_1 - l2*m2*w2**2*(cos_1*sin_2 - cos_2*sin_1) - l2*m3*w2**2*(cos_1*sin_2 - cos_2*sin_1) - l3*m3*w3**2*(cos_1*sin_3 - cos_3*sin_1)) - (-cos_21*cos_31*m2 - cos_21*cos_31*m3 + cos_32*m1 + cos_32*m2 + cos_32*m3)*(g*m2*sin_2 + g*m3*sin_2 + l1*m2*w1**2*(cos_1*sin_2 - cos_2*sin_1) + l1*m3*w1**2*(cos_1*sin_2 - cos_2*sin_1) - l3*m3*w3**2*(cos_2*sin_3 - cos_3*sin_2)))/(l3*(cos_21**2*m2**2 + 2*cos_21**2*m2*m3 + cos_21**2*m3**2 - 2*cos_21*cos_31*cos_32*m2*m3 - 2*cos_21*cos_31*cos_32*m3**2 + cos_31**2*m2*m3 + cos_31**2*m3**2 + cos_32**2*m1*m3 + cos_32**2*m2*m3 + cos_32**2*m3**2 - m1*m2 - m1*m3 - m2**2 - 2*m2*m3 - m3**2))

	return np.array([ w1, w2, w3 , dw1, dw2, dw3])


def f_double( u , t):
	theta_1, theta_2 = u[0], u[1]
	w1, w2 = u[3], u[4]

	theta_12 = theta_1 - theta_2

	cos_12 = np.cos(theta_12)
	sin_12 = np.sin(theta_12)
	sin_1, sin_2 = (np.sin(theta_1), np.sin(theta_2))
	cos_1, cos_2 = (np.cos(theta_1), np.cos(theta_2))

	dw1 = (-sin_12*(m2*l1*w1**2 * cos_12 + m2*l2*w2**2) - g*((m1+m2)*sin_1 - m2*sin_2 * cos_12))/(l1*(m1 + m2* sin_12**2))
	dw2 = (sin_12 * ((m1+m2)*l1*w1**2 + m2*l2*w2**2 * cos_12) + g*((m1+m2)*sin_1 * cos_12 - (m1+m2)*sin_2))/(l2*(m1+m2*sin_12**2))   

	return np.array([ w1, w2, 0, dw1, dw2, 0])


def f_single( u , t):
	theta_1 = u[0]
	w1 = u[1]      
	dw1 = -g/l1 * np.sin(theta_1)
	return np.array([ w1, 0, 0, dw1, 0, 0])



def get_xy_coords(q):
	x1 = l1*np.sin(q[0])
	x2 = l2*np.sin(q[1]) + x1
	x3 = l3 * np.sin(q[2]) + x2
	y1 = -l1*np.cos(q[0]) 
	y2 = -l2*np.cos(q[1]) + y1 
	y3 = -l3 * np.cos(q[2]) + y2
	x = (x1, x2, x3)
	y = (y1, y2, y3)
	return x, y 

def get_polar_coords(p):
	x, y = get_xy_coords(p)
	r1 = np.sqrt(x[0]*x[0] + y[0]*y[0])
	r2 = np.sqrt(x[1]*x[1] + y[1]*y[1])
	r3 = np.sqrt(x[2]*x[2] + y[2]*y[2])
	return (p[0], p[1], p[2]), (r1, r2, r3)


def get_xy_velocity(p):
	dx1 = -l1*np.cos(p[0])*p[3]
	dx2 = -l2*np.cos(p[1])*p[4] + dx1
	dx3 = -l3 * np.cos(p[2])*p[5] + dx2
	dy1 = -l1*np.sin(p[0])*p[3]
	dy2 = -l2*np.sin(p[1])*p[4] + dy1 
	dy3 = -l3 * np.sin(p[2])*p[5] + dy2
	return (dx1, dx2, dx3), (dy1, dy2, dy3)

def energia_cinetica(p):
	dx, dy = get_xy_velocity(p)
	dx1 = -l1*np.cos(p[0])*p[3]
	dx2 = -l2*np.cos(p[1])*p[4] + dx1
	dx3 = -l3 * np.cos(p[2])*p[5] + dx2
	dy1 = -l1*np.sin(p[0])*p[3] 
	dy2 =  -l2*np.sin(p[1])*p[4] + dy1 
	dy3 = -l3 * np.sin(p[2])*p[5] + dy2
	ek = (dx[0]**2 + dx[1]**2 + dx[2]**2 + dy[0]**2 + dy[1]**2 + dy[2]**2)/2.
	return ek

def energia_potenziale(p):
	x, y = get_xy_coords(p)
	ep = g*(m1*y[0]+m2*y[1]+m3*y[2])
	return ep

def energia_totale(p):
	return energia_cinetica(p) + energia_potenziale(p)
    
def plot_pendulum(x, y):
	zeros = np.zeros(np.shape(np.atleast_2d(x[0]).T))
	x = np.hstack([zeros, np.atleast_2d(x[0]).T, np.atleast_2d(x[1]).T, np.atleast_2d(x[2]).T])
	y = np.hstack([zeros, np.atleast_2d(y[0]).T, np.atleast_2d(y[1]).T, np.atleast_2d(y[2]).T])
	return x, y

def animate_triple_pendulum(f, output):
    global t, tempo_simulazione, h
    u0 = np.array([theta0_1, theta0_2, theta0_3, w0_1, w0_2, w0_3])
    um1 = np.array([theta0_1, theta0_2, theta0_3, w0_1, w0_2, w0_3])
    u = np.array([u0, um1])
    count = 0
    while(t<=tempo_simulazione):
        u = f(f_triple, u)
        t+=h
        if(count % fps60 == 0):
            u0_plot.append(copy.deepcopy(u[0]))
            print(u[0])
        count+=1
        #print(count)
    fps= punti/tempo_simulazione
    fig = plt.figure()
    ax_pend = plt.subplot(331)
    #                            gridspec_kw={
    #                           'width_ratios': [2, 1, 1],
    #                           'height_ratios': [2, 1, 1]})
    ax_polar = fig.add_subplot(332, projection='polar')
    ax_3d = fig.add_subplot(333, projection='3d')
    ax_en_tot = fig.add_subplot(334)
    ax_en_k_p = fig.add_subplot(335)


    ax_pend.set_aspect('equal', adjustable='box')
    ax_pend.axis('off')
    ax_pend.set(xlim=(-(l1+l2+l3)*1.2, (l1+l2+l3)*1.2), ylim=(-(l1+l2+l3)*1.2, (l1+l2+l3)*1.2))

    line, = ax_pend.plot([], [], 'o-', lw=2)    
    time_text = ax_pend.text(0.02, 0.95, '', transform=ax_pend.transAxes)
    energy_text = ax_pend.text(0.02, 0.90, '', transform=ax_pend.transAxes)


    #    fig = plt.figure()

    # to change size of subplot's
    # set height of each subplot as 8
    fig.set_figheight(8)

    # set width of each subplot as 8
    fig.set_figwidth(8)
     
    def init():
        line.set_data([], [])
        time_text.set_text('')
        energy_text.set_text('')
        return line, time_text, energy_text

    def animate(i):
        i = int(i*fps)
        f(f_triple)
        x, y = get_xy_coords(u0)
        xplot, yplot = plot_pendulum(x,y)
        theta, r = get_polar_coords(u0)
        en_tot = energia_totale(u0)

        line.set_data(xplot, yplot)
        time_text.set_text('time = %.1f' % ((tempo_simulazione)*i/punti))
        energy_text.set_text('energy = %.9f J' % en_tot)
        
        ax_3d.plot((r[0]*np.sin(theta[0])), (r[0]*np.cos(theta[0])), t)
        ax_3d.plot((r[1]*np.sin(theta[1])), (r[1]*np.cos(theta[1])), t)
        ax_3d.plot((r[2]*np.sin(theta[2])), (r[2]*np.cos(theta[2])), t)


        ax_polar.plot(theta[0], r[0])
        ax_polar.plot(theta[1], r[1])
        ax_polar.plot(theta[2], r[2])

        ax_en_tot.plot(t, energia_totale(u0), label='Energia Totale')
        ax_en_k_p.plot(t, energia_cinetica(u0), label='Energia Cinetica')
        ax_en_k_p.plot(t, energia_potenziale(u0), label='Energia Potenziale')
        return mplfig_to_npimage(fig)
    
    duration = tempo_simulazione
    animation = mpy.VideoClip(animate, duration=duration)
    # animation.write_gif('matplotlib.gif', fps= fps)
    animation.write_videofile(output, fps = fps/1000 )
    # animation.ipython_display(fps= fps, loop=True, autoplay=True)
    #cmap='hsv'

    return animation


anim_pend = animate_triple_pendulum(stormer_verlet, "sv_triple.mp4")
#anim_pend = animate_single_pendulum(stormer_verlet, "sv_single.mp4")
#anim_pend = animate_double_pendulum(velocity_verlet, "vv_double.mp4")
#anim_pend = animate_triple_pendulum(runge_kutta4, "rk.mp4")
#

[ 7.85398161e-01  5.23598776e-01  4.18879021e-01 -1.49491719e-04
  6.16971252e-05  1.83521032e-05]
[ 7.85398161e-01  5.23598776e-01  4.18879021e-01 -1.49491719e-04
  6.16971252e-05  1.83521032e-05]
[ 7.85398159e-01  5.23598777e-01  4.18879021e-01 -2.49152865e-04
  1.02828546e-04  3.05868386e-05]
[ 7.85398155e-01  5.23598779e-01  4.18879021e-01 -3.48814011e-04
  1.43959966e-04  4.28215741e-05]
[ 7.85398151e-01  5.23598781e-01  4.18879022e-01 -4.48475157e-04
  1.85091387e-04  5.50563095e-05]
[ 7.85398145e-01  5.23598783e-01  4.18879023e-01 -5.48136303e-04
  2.26222807e-04  6.72910450e-05]
[ 7.85398139e-01  5.23598786e-01  4.18879023e-01 -6.47797449e-04
  2.67354228e-04  7.95257804e-05]
[ 7.85398132e-01  5.23598789e-01  4.18879024e-01 -7.47458595e-04
  3.08485648e-04  9.17605159e-05]
[ 7.85398123e-01  5.23598792e-01  4.18879025e-01 -8.47119741e-04
  3.49617058e-04  1.03995251e-04]
[ 7.85398114e-01  5.23598796e-01  4.18879027e-01 -9.46780876e-04
  3.90748467e-04  1.16229987e-04]
[ 7.853981

[ 0.78514839  0.52370186  0.4189097  -0.07050739  0.02909769  0.00866235]
[ 0.78514768  0.52370215  0.41890978 -0.07060704  0.02913881  0.00867461]
[ 0.78514697  0.52370244  0.41890987 -0.07070668  0.02917993  0.00868687]
[ 0.78514626  0.52370273  0.41890996 -0.07080633  0.02922105  0.00869913]
[ 0.78514556  0.52370303  0.41891004 -0.07090598  0.02926217  0.00871139]
[ 0.78514485  0.52370332  0.41891013 -0.07100563  0.02930329  0.00872365]
[ 0.78514413  0.52370361  0.41891022 -0.07110528  0.02934441  0.00873592]
[ 0.78514342  0.52370391  0.41891031 -0.07120493  0.02938553  0.00874818]
[ 0.78514271  0.5237042   0.41891039 -0.07130458  0.02942665  0.00876044]
[ 0.785142    0.5237045   0.41891048 -0.07140423  0.02946777  0.0087727 ]
[ 0.78514128  0.52370479  0.41891057 -0.07150387  0.02950889  0.00878496]
[ 0.78514056  0.52370509  0.41891066 -0.07160352  0.02955     0.00879723]
[ 0.78513985  0.52370538  0.41891074 -0.07170317  0.02959112  0.00880949]
[ 0.78513913  0.52370568  0.41891083 -

[ 0.78442991  0.52399834  0.41899806 -0.13885573  0.05729514  0.01709709]
[ 0.78442853  0.52399891  0.41899823 -0.13895534  0.05733622  0.01710943]
[ 0.78442713  0.52399949  0.4189984  -0.13905496  0.0573773   0.01712177]
[ 0.78442574  0.52400006  0.41899858 -0.13915457  0.05741839  0.0171341 ]
[ 0.78442435  0.52400064  0.41899875 -0.13925418  0.05745947  0.01714644]
[ 0.78442296  0.52400121  0.41899892 -0.13935379  0.05750056  0.01715878]
[ 0.78442156  0.52400179  0.41899909 -0.13945341  0.05754164  0.01717112]
[ 0.78442017  0.52400236  0.41899926 -0.13955302  0.05758273  0.01718346]
[ 0.78441877  0.52400294  0.41899943 -0.13965263  0.05762381  0.0171958 ]
[ 0.78441737  0.52400352  0.41899961 -0.13975225  0.05766489  0.01720814]
[ 0.78441597  0.52400409  0.41899978 -0.13985186  0.05770598  0.01722048]
[ 0.78441457  0.52400467  0.41899995 -0.13995147  0.05774706  0.01723282]
[ 0.78441317  0.52400525  0.41900012 -0.14005108  0.05778815  0.01724516]
[ 0.78441177  0.52400583  0.4190003  -

[ 0.78319266  0.52450879  0.41915069 -0.20956029  0.08644449  0.02590108]
[ 0.78319056  0.52450965  0.41915095 -0.20965984  0.08648551  0.02591355]
[ 0.78318846  0.52451052  0.41915121 -0.20975939  0.08652653  0.02592602]
[ 0.78318636  0.52451139  0.41915147 -0.20985894  0.08656755  0.02593849]
[ 0.78318427  0.52451225  0.41915173 -0.20995849  0.08660857  0.02595096]
[ 0.78318216  0.52451312  0.41915199 -0.21005804  0.08664959  0.02596343]
[ 0.78318006  0.52451398  0.41915225 -0.21015759  0.08669061  0.02597591]
[ 0.78317796  0.52451485  0.41915251 -0.21025714  0.08673164  0.02598838]
[ 0.78317586  0.52451572  0.41915277 -0.21035669  0.08677266  0.02600085]
[ 0.78317375  0.52451659  0.41915303 -0.21045623  0.08681368  0.02601332]
[ 0.78317165  0.52451746  0.41915329 -0.21055578  0.0868547   0.0260258 ]
[ 0.78316954  0.52451833  0.41915355 -0.21065533  0.08689572  0.02603827]
[ 0.78316743  0.52451919  0.41915381 -0.21075488  0.08693674  0.02605074]
[ 0.78316532  0.52452006  0.41915407 -

[ 0.78152334  0.52519725  0.41935755 -0.27772263  0.11451427  0.03450242]
[ 0.78152056  0.5251984   0.41935789 -0.27782209  0.1145552   0.03451507]
[ 0.78151778  0.52519954  0.41935824 -0.27792155  0.11459613  0.03452772]
[ 0.781515    0.52520069  0.41935858 -0.27802101  0.11463706  0.03454037]
[ 0.78151222  0.52520183  0.41935893 -0.27812047  0.11467799  0.03455302]
[ 0.78150944  0.52520298  0.41935928 -0.27821993  0.11471891  0.03456568]
[ 0.78150665  0.52520413  0.41935962 -0.27831938  0.11475984  0.03457833]
[ 0.78150387  0.52520528  0.41935997 -0.27841884  0.11480077  0.03459098]
[ 0.78150108  0.52520643  0.41936031 -0.2785183   0.1148417   0.03460364]
[ 0.7814983   0.52520757  0.41936066 -0.27861776  0.11488262  0.03461629]
[ 0.78149551  0.52520872  0.41936101 -0.27871722  0.11492355  0.03462894]
[ 0.78149272  0.52520987  0.41936135 -0.27881667  0.11496448  0.0346416 ]
[ 0.78148993  0.52521102  0.4193617  -0.27891613  0.11500541  0.03465425]
[ 0.78148714  0.52521217  0.41936205 -

...

[-0.23932469 -0.18969188 -0.51838563 -0.84097384  0.43006429 -3.88215545]
[-0.2393331  -0.18968758 -0.51842445 -0.84093489  0.42997089 -3.88205334]
[-0.23934151 -0.18968328 -0.51846327 -0.84089594  0.42987748 -3.88195122]
[-0.23934992 -0.18967898 -0.51850209 -0.84085699  0.42978406 -3.8818491 ]
[-0.23935832 -0.18967469 -0.51854091 -0.84081803  0.42969063 -3.88174697]
[-0.23936673 -0.18967039 -0.51857972 -0.84077906  0.4295972  -3.88164483]
[-0.23937514 -0.1896661  -0.51861854 -0.8407401   0.42950375 -3.88154269]
[-0.23938355 -0.1896618  -0.51865735 -0.84070113  0.4294103  -3.88144054]
[-0.23939195 -0.18965751 -0.51869617 -0.84066215  0.42931684 -3.88133838]
[-0.23940036 -0.18965322 -0.51873498 -0.84062317  0.42922337 -3.88123622]
[-0.23940877 -0.18964893 -0.51877379 -0.84058419  0.4291299  -3.88113405]
[-0.23941717 -0.18964464 -0.5188126  -0.84054521  0.42903641 -3.88103187]
[-0.23942558 -0.18964035 -0.51885141 -0.84050622  0.42894292 -3.88092969]
[-0.23943398 -0.18963606 -0.51889022 -

[-0.24500002 -0.186966   -0.54477333 -0.81340697  0.36416571 -3.81070923]
[-0.24500815 -0.18696236 -0.54481144 -0.81336562  0.3640672  -3.81060321]
[-0.24501629 -0.18695872 -0.54484954 -0.81332426  0.36396867 -3.81049718]
[-0.24502442 -0.18695508 -0.54488765 -0.8132829   0.36387014 -3.81039115]
[-0.24503255 -0.18695144 -0.54492575 -0.81324154  0.36377161 -3.81028511]
[-0.24504069 -0.1869478  -0.54496385 -0.81320017  0.36367307 -3.81017907]
[-0.24504882 -0.18694417 -0.54500195 -0.8131588   0.36357452 -3.81007302]
[-0.24505695 -0.18694053 -0.54504005 -0.81311743  0.36347596 -3.80996696]
[-0.24506508 -0.1869369  -0.54507815 -0.81307605  0.3633774  -3.80986091]
[-0.24507321 -0.18693327 -0.54511625 -0.81303467  0.36327883 -3.80975484]
[-0.24508134 -0.18692963 -0.54515434 -0.81299329  0.36318026 -3.80964877]
[-0.24508947 -0.186926   -0.54519244 -0.8129519   0.36308168 -3.8095427 ]
[-0.2450976  -0.18692237 -0.54523053 -0.81291052  0.36298309 -3.80943662]
[-0.24510573 -0.18691874 -0.54526863 -

[-0.25037106 -0.18474467 -0.5701392  -0.78493978  0.29661665 -3.73843606]
[-0.25037891 -0.1847417  -0.57017658 -0.78489647  0.2965143  -3.73832712]
[-0.25038676 -0.18473874 -0.57021396 -0.78485316  0.29641196 -3.73821818]
[-0.25039461 -0.18473577 -0.57025134 -0.78480984  0.2963096  -3.73810923]
[-0.25040245 -0.18473281 -0.57028872 -0.78476652  0.29620724 -3.73800028]
[-0.2504103  -0.18472985 -0.5703261  -0.7847232   0.29610488 -3.73789133]
[-0.25041815 -0.18472689 -0.57036348 -0.78467988  0.29600251 -3.73778237]
[-0.25042599 -0.18472393 -0.57040086 -0.78463656  0.29590014 -3.73767341]
[-0.25043384 -0.18472097 -0.57043823 -0.78459323  0.29579776 -3.73756444]
[-0.25044168 -0.18471802 -0.57047561 -0.7845499   0.29569538 -3.73745547]
[-0.25044953 -0.18471506 -0.57051298 -0.78450656  0.29559299 -3.7373465 ]
[-0.25045737 -0.1847121  -0.57055035 -0.78446323  0.29549059 -3.73723752]
[-0.25046522 -0.18470915 -0.57058772 -0.78441989  0.2953882  -3.73712854]
[-0.25047306 -0.1847062  -0.57062509 -

[-0.2556448  -0.18295572 -0.59548968 -0.7546968   0.2254844  -3.66302575]
[-0.25565235 -0.18295346 -0.5955263  -0.75465186  0.22537922 -3.66291463]
[-0.25565989 -0.18295121 -0.59556293 -0.75460693  0.22527404 -3.66280351]
[-0.25566744 -0.18294896 -0.59559956 -0.75456199  0.22516885 -3.66269239]
[-0.25567498 -0.18294671 -0.59563619 -0.75451705  0.22506367 -3.66258126]
[-0.25568253 -0.18294446 -0.59567281 -0.75447211  0.22495848 -3.66247013]
[-0.25569007 -0.18294221 -0.59570943 -0.75442716  0.22485328 -3.662359  ]
[-0.25569762 -0.18293996 -0.59574606 -0.75438221  0.22474809 -3.66224787]
[-0.25570516 -0.18293772 -0.59578268 -0.75433726  0.22464288 -3.66213673]
[-0.2557127  -0.18293547 -0.5958193  -0.75429231  0.22453768 -3.6620256 ]
[-0.25572024 -0.18293323 -0.59585592 -0.75424736  0.22443247 -3.66191445]
[-0.25572779 -0.18293098 -0.59589254 -0.7542024   0.22432726 -3.66180331]
[-0.25573533 -0.18292874 -0.59592915 -0.75415745  0.22422205 -3.66169216]
[-0.25574287 -0.1829265  -0.59596577 -

KeyboardInterrupt: 